<a href="https://colab.research.google.com/github/TheViet298/BTL_NMKHDL/blob/main/Crawling_data.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%%capture
# Cài đặt thư viện cần thiết
!pip3 install pandas;
!pip3 install tqdm;
!pip3 install bs4;
!pip3 install regex;
!pip3 install numpy;
!pip3 install pyvi;
!pip3 install gensim;
!pip3 install matplotlib;
!pip3 install seaborn;
!pip3 install -U scikit-learn;
!pip3 install lime;
!pip3 install

In [2]:
%matplotlib inline
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = [12, 8]
plt.rcParams['figure.dpi'] = 125

import seaborn as sns

import pandas as pd
import numpy as np
np.random.seed(0) # Chạy các hàm của scikit-learn giống nhau mỗi lần chạy

import regex as re
import time
from tqdm.notebook import tqdm # Hiện thanh progress cho đẹp :D
tqdm.pandas()

# Thư viện để request và parse HTML
import requests
from bs4 import BeautifulSoup

# Các thư viện liên quan tới ngôn ngữ và NLP
from pyvi import ViTokenizer
import gensim
import unicodedata

# Trực quan hóa mô hình dự đoán văn bản
from lime import lime_text

# Lưu lại model
import pickle

# Thư viện liên quan của Scikit-learn
from sklearn.model_selection import train_test_split
from sklearn.metrics import ConfusionMatrixDisplay # vẽ ma trận nhầm lẫn
from sklearn.preprocessing import LabelEncoder

from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn import feature_selection

# Tạo pipeline
from sklearn.preprocessing import FunctionTransformer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline
from sklearn.compose import make_column_transformer, make_column_selector

# Các mô hình học
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import BaggingClassifier # Phương pháp bagging

In [3]:
# Thiết lập đường dẫn cho phần 1
dir_1 = "src/scraped_data/"

In [5]:
# Thử nghiệm url đầu tiên
url = "https://tuoitre.vn/tin-moi-nhat.htm"

# Lấy danh sách box-category-item
html_text = requests.get(url).text
html_tree = BeautifulSoup(html_text, 'html.parser')
news_items = html_tree.find_all('div', class_='box-category-item')

# tạo df
data = []

# Lấy ra các trường từ box-category-item
for item in news_items:
  title_t = item.find('a', class_='box-category-link-title') # Tiêu đề
  category_t = item.find('a', class_= 'box-category-category') # Thể loại
  description_t = item.find('div', class_= 'box-category-content') # mô tả

  # Kiểm tra nếu tìm thấy các trường
  if title_t and category_t:
    title = title_t.text.strip()
    link = "https://tuoitre.vn" + title_t.get("href", "")
    category = category_t.text.strip()
    # thêm dữ liệu các trường vào data
    data.append({"links": link, "title": title,"description": "Null","content": "Null", "class": category})

# Chuyển danh sách thành DataFrame
raw_data = pd.DataFrame(data)

raw_data.tail()
# print(raw_data.head())

links  \
15  https://tuoitre.vn/evnspc-5-ngay-dong-dien-10-...   
16  https://tuoitre.vn/diem-tin-18h-tp-hcm-ra-soat...   
17  https://tuoitre.vn/ca-si-trung-quoc-phuong-dai...   
18  https://tuoitre.vn/100-doi-sinh-vien-do-suc-th...   
19  https://tuoitre.vn/hang-du-muc-va-quang-linh-v...   

                                                title description content  \
15   EVNSPC 5 ngày đóng điện 10 công trình thành công        Null    Null   
16  Điểm tin 18h: TP.HCM rà soát đèn giao thông; '...        Null    Null   
17  Ca sĩ Trung Quốc Phương Đại Đồng qua đời ở tuổ...        Null    Null   
18        100 đội sinh viên đọ sức thiết kế xe hybrid        Null    Null   
19  Hằng Du Mục và Quang Linh Vlogs bị tố quảng cá...        Null    Null   

         class  
15    Cần biết  
16    Cần biết  
17     Văn hóa  
18    Giáo dục  
19  Kinh doanh

In [11]:
%%time
for _, row in raw_data.iterrows():
    try:
        # Gửi request để lấy nội dung trang bài viết
        news_page = requests.get(row["links"]).content
        news_tree = BeautifulSoup(news_page, "html.parser")

        # Lấy mô tả (description)
        try:
            row["description"] = news_tree.find("h2", class_="detail-sapo").text.strip()
        except:
            row["description"] = ''

        # Kiểm tra nếu bài viết là dạng "điểm tin" hoặc "video" (không có nội dung chính)
        body = news_tree.find("div", class_="detail-content afcbc-body readmore-body")

        if body:  # Nếu có thẻ nội dung thì lấy text
            content = body.find_all("p", recursive=False)
            row["content"] = "\n".join([x.text.strip() for x in content])
        else:  # Nếu không có thẻ nội dung chính, gán content là ''
            row["content"] = ''

    except requests.exceptions.RequestException as e:
        print(f"Lỗi request {row['links']}: {e}")
        row["description"], row["content"] = '', ''

    time.sleep(0.05)

# raw_data.tail()
print(raw_data.head())

                                               links  \
0  https://tuoitre.vn/san-sang-cho-khai-hoi-tu-va...   
1  https://tuoitre.vn/truong-dai-hoc-quoc-te-dai-...   
2  https://tuoitre.vn/he-lo-thuc-don-hoanh-trang-...   
3  https://tuoitre.vn/clb-cong-an-ha-noi-khong-th...   
4  https://tuoitre.vn/campuchia-truc-xuat-119-ngu...   

                                               title  \
0  Sẵn sàng chờ 'khai hội' tư vấn tuyển sinh tại ...   
1  Trường đại học Quốc tế - Đại học Quốc gia TP.H...   
2  Hé lộ thực đơn hoành tráng, xa hoa cho bữa tiệ...   
3  CLB Công An Hà Nội không thắng nổi đội áp chót...   
4  Campuchia trục xuất 119 người Thái Lan sau cuộ...   

                                         description  \
0  Các trường đại học, cao đẳng... đã hoàn tất nh...   
1  Năm 2025, Trường đại học Quốc tế (Đại học Quốc...   
2  Wolfgang Puck tiết lộ rằng hầu hết các ngôi sa...   
3  Thủ môn Nguyễn Văn Việt cứu thua cho Sông Lam ...   
4  Ngày 1-3, Campuchia thông báo quốc gia này 

In [12]:
raw_data.tail()

links  \
15  https://tuoitre.vn/evnspc-5-ngay-dong-dien-10-...   
16  https://tuoitre.vn/diem-tin-18h-tp-hcm-ra-soat...   
17  https://tuoitre.vn/ca-si-trung-quoc-phuong-dai...   
18  https://tuoitre.vn/100-doi-sinh-vien-do-suc-th...   
19  https://tuoitre.vn/hang-du-muc-va-quang-linh-v...   

                                                title  \
15   EVNSPC 5 ngày đóng điện 10 công trình thành công   
16  Điểm tin 18h: TP.HCM rà soát đèn giao thông; '...   
17  Ca sĩ Trung Quốc Phương Đại Đồng qua đời ở tuổ...   
18        100 đội sinh viên đọ sức thiết kế xe hybrid   
19  Hằng Du Mục và Quang Linh Vlogs bị tố quảng cá...   

                                          description  \
15  Chỉ từ ngày 23 đến 27-2-2025, hàng loạt công t...   
16  Điểm tin 18h ngày 1-3-2025: Tàu hỏa trật bánh ...   
17  Phương Đại Đồng - ca sĩ, nhạc sĩ nổi tiếng Tru...   
18  Sau khi tự thiết kế các chiếc xe đua, các đội ...   
19  Nổi tiếng trên mạng, được yêu mến với hàng tri...   

                                              content       class  
15                                                       Cần biết  
16                                           Điểm tin    Cần biết  
17  Chiều 1-3, Sohu đưa tin sau 5 năm chiến đấu vớ...     Văn hóa  
18  Ngày 1-3-2025, tại Trường cao đẳng Kỹ thuật Ca...    Giáo dục  
19  Hằng Du Mục (tên thật là Nguyễn Thị Thái Hằng)...  Kinh doanh

from matplotlib import pyplot as plt
import seaborn as sns
_df_0.groupby('links').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_1.groupby('title').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_2.groupby('description').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_3.groupby('content').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['title'].value_counts()
    for x_label, grp in _df_4.groupby('links')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('links')
_ = plt.ylabel('title')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['description'].value_counts()
    for x_label, grp in _df_5.groupby('title')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('title')
_ = plt.ylabel('description')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['content'].value_counts()
    for x_label, grp in _df_6.groupby('description')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('description')
_ = plt.ylabel('content')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['class'].value_counts()
    for x_label, grp in _df_7.groupby('content')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('content')
_ = plt.ylabel('class')